In [1]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np

In [2]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
req = requests.get(url).text
soup = BeautifulSoup(req, 'html')

## Let's read the contents of the web page and look for the cells

In [3]:
# The contents of the table cell for reference
print(soup.find_all('td')[6].text)
soup.find_all('td')[6]


M7AQueen's Park(Ontario Provincial Government)




<td style="width:11%; vertical-align:top;">
<p><b>M7A</b><br/><span style="font-size:85%;"><a href="/wiki/Queen%27s_Park_(Toronto)" title="Queen's Park (Toronto)">Queen's Park</a><br/>(Ontario Provincial Government)</span>
</p>
</td>

In [4]:
# First let's make a list that will contain all the information
comm = []
# Run through all the instances of a table cell
for instance in soup.find_all('td'):
    # Initiate the dictionary that will hold the cell's data
    commDict = {}
    # The try will kick out if there is no information in the cell and make no entry
    try:
        # The postal code is wrapped up in the first Bold tag <b></b>
        commDict['PostalCode'] = instance.b.text
        # If the cell is unassaigned it will not allocate any information
        if instance.span.text == 'Not assigned':
            pass
        else:
            data = instance.span.text.split(')')
            # Now the Borough is in the first bit of the text before the '('
            commDict['Borough'] = instance.span.text[:instance.span.text.find('(')]
            commDict['Neighborhood'] = ''
            for area in data:
                if commDict['Neighborhood'] != '' and len(area.split('(')>1):
                    commDict['Neighborhood'] = commDict['Neighborhood'] + ',' 
                # The neighborhoods content is in between the cells and seperated by ' / '
                commDict['Neighborhood'] = commDict['Neighborhood'] + area[instance.span.text.find('(')+1:].replace(' / ',',')
    except:
        pass
    # Now we read the data into the list 'comm' if there is information
    try:
        if commDict['Borough'] is not None:
            comm.append(commDict)
    except:
        pass

In [5]:
# Now we read the dictionary into a dataframe
df_scrape = pd.DataFrame(comm)
df_scrape

PostalCode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A                                       Queen's Park   
..         ...                                                ...   
98         M8X                                          Etobicoke   
99         M4Y                                   Downtown Toronto   
100        M7Y  East TorontoBusiness reply mail Processing Cen...   
101        M8Y                                          Etobicoke   
102        M8Z                                          Etobicoke   

                                          Neighborhood  
0                                            Parkwoods  
1                                     Victoria Village  
2                             Regent Park,Harbourfront  
3                      Lawrence Manor,Lawrence Heights  
4                        Ontario Provincial Government  
..                                                 ...  
98         The Kingsway,Montgomery Road,Old Mill North  
99                                Church and Wellesley  
100                                     Enclave of M4L  
101  Old Mill South,King's Mill Park,Sunnylea,Humbe...  
102  Mimico NW,The Queensway West,South of Bloor,Ki...  

[103 rows x 3 columns]

In [6]:
# Let's remove areas that are just postal addresses
ban_list = ['M7Y','M5W','M7R','M7A']
df_scrape = df_scrape[~df_scrape['PostalCode'].isin(ban_list)]
df_scrape.shape

(99, 3)

In [7]:
import geocoder # import geocoder

df_PScodes = pd.read_csv("https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs_v1/Geospatial_Coordinates.csv")
df_PScodes = df_PScodes.set_index('Postal Code')
df_PScodes

Latitude  Longitude
Postal Code                      
M1B          43.806686 -79.194353
M1C          43.784535 -79.160497
M1E          43.763573 -79.188711
M1G          43.770992 -79.216917
M1H          43.773136 -79.239476
...                ...        ...
M9N          43.706876 -79.518188
M9P          43.696319 -79.532242
M9R          43.688905 -79.554724
M9V          43.739416 -79.588437
M9W          43.706748 -79.594054

[103 rows x 2 columns]

Now if we make the indexes the same for the two dataframes we will have the new columns automatically take on the correct values for the postal codes.

In [8]:
df_scrape = df_scrape.set_index('PostalCode')
df_scrape['Latitude'], df_scrape['Longitude'] = df_PScodes['Latitude'], df_PScodes['Longitude']
df_scrape

Borough  \
PostalCode                     
M3A               North York   
M4A               North York   
M5A         Downtown Toronto   
M6A               North York   
M9A                Etobicoke   
...                      ...   
M5X         Downtown Toronto   
M8X                Etobicoke   
M4Y         Downtown Toronto   
M8Y                Etobicoke   
M8Z                Etobicoke   

                                                 Neighborhood   Latitude  \
PostalCode                                                                 
M3A                                                 Parkwoods  43.753259   
M4A                                          Victoria Village  43.725882   
M5A                                  Regent Park,Harbourfront  43.654260   
M6A                           Lawrence Manor,Lawrence Heights  43.718518   
M9A                                          Islington Avenue  43.667856   
...                                                       ...        ...   
M5X                     First Canadian Place,Underground city  43.648429   
M8X               The Kingsway,Montgomery Road,Old Mill North  43.653654   
M4Y                                      Church and Wellesley  43.665860   
M8Y         Old Mill South,King's Mill Park,Sunnylea,Humbe...  43.636258   
M8Z         Mimico NW,The Queensway West,South of Bloor,Ki...  43.628841   

            Longitude  
PostalCode             
M3A        -79.329656  
M4A        -79.315572  
M5A        -79.360636  
M6A        -79.464763  
M9A        -79.532242  
...               ...  
M5X        -79.382280  
M8X        -79.506944  
M4Y        -79.383160  
M8Y        -79.498509  
M8Z        -79.520999  

[99 rows x 4 columns]

In [9]:
df_scrape.reset_index(inplace=True)

In [10]:
df_scrape

PostalCode           Borough  \
0         M3A        North York   
1         M4A        North York   
2         M5A  Downtown Toronto   
3         M6A        North York   
4         M9A         Etobicoke   
..        ...               ...   
94        M5X  Downtown Toronto   
95        M8X         Etobicoke   
96        M4Y  Downtown Toronto   
97        M8Y         Etobicoke   
98        M8Z         Etobicoke   

                                         Neighborhood   Latitude  Longitude  
0                                           Parkwoods  43.753259 -79.329656  
1                                    Victoria Village  43.725882 -79.315572  
2                            Regent Park,Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor,Lawrence Heights  43.718518 -79.464763  
4                                    Islington Avenue  43.667856 -79.532242  
..                                                ...        ...        ...  
94              First Canadian Place,Underground city  43.648429 -79.382280  
95        The Kingsway,Montgomery Road,Old Mill North  43.653654 -79.506944  
96                               Church and Wellesley  43.665860 -79.383160  
97  Old Mill South,King's Mill Park,Sunnylea,Humbe...  43.636258 -79.498509  
98  Mimico NW,The Queensway West,South of Bloor,Ki...  43.628841 -79.520999  

[99 rows x 5 columns]

In [11]:
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

In [12]:
address = 'Toronto, Canada'

latitude = df_scrape['Latitude'].mean()

In [13]:
longitude = df_scrape['Longitude'].mean()
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.70672879191919, -79.39601043535355.


In [14]:
# create map of New York using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11.4)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_scrape['Latitude'], df_scrape['Longitude'], df_scrape['Borough'], df_scrape['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [15]:
CLIENT_ID = '24XQ2KIMXRYFZEWHRQZ1TSNKKDPFSLILAR1QNI1XPZREE5IF' # your Foursquare ID
CLIENT_SECRET = '4USSMOW03WWKLQEU5RWGMFPD3RSTDCNUS2KUUB0HEYUMAJGT' # your Foursquare Secret
ACCESS_TOKEN = 'BC2RNYUFSVGTBESYEFA1BZHJ1LMEBA5TXOZ1U2ZAJWXTRZZ1' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 24XQ2KIMXRYFZEWHRQZ1TSNKKDPFSLILAR1QNI1XPZREE5IF
CLIENT_SECRET:4USSMOW03WWKLQEU5RWGMFPD3RSTDCNUS2KUUB0HEYUMAJGT


In [16]:
def getNearbyVenues(names, latitudes, longitudes, radius=1300):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [17]:
toronto_venues = getNearbyVenues(names=df_scrape['PostalCode'],
                                   latitudes=df_scrape['Latitude'],
                                   longitudes=df_scrape['Longitude']
                                  )

M3A
M4A
M5A
M6A
M9A
M1B
M3B
M4B
M5B
M6B
M9B
M1C
M3C
M4C
M5C
M6C
M9C
M1E
M4E
M5E
M6E
M1G
M4G
M5G
M6G
M1H
M2H
M3H
M4H
M5H
M6H
M1J
M2J
M3J
M4J
M5J
M6J
M1K
M2K
M3K
M4K
M5K
M6K
M1L
M2L
M3L
M4L
M5L
M6L
M9L
M1M
M2M
M3M
M4M
M5M
M6M
M9M
M1N
M2N
M3N
M4N
M5N
M6N
M9N
M1P
M2P
M4P
M5P
M6P
M9P
M1R
M2R
M4R
M5R
M6R
M9R
M1S
M4S
M5S
M6S
M1T
M4T
M5T
M1V
M4V
M5V
M8V
M9V
M1W
M4W
M8W
M9W
M1X
M4X
M5X
M8X
M4Y
M8Y
M8Z


In [35]:
toronto_venues.shape

(2739, 7)

In [36]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0          M3A              43.753259              -79.329656   
1          M3A              43.753259              -79.329656   
2          M3A              43.753259              -79.329656   
3          M3A              43.753259              -79.329656   
4          M3A              43.753259              -79.329656   

                         Venue  Venue Latitude  Venue Longitude  \
0              Allwyn's Bakery       43.759840       -79.324719   
1              Brookbanks Park       43.751976       -79.332140   
2                  Tim Hortons       43.760668       -79.326368   
3  Donalda Golf & Country Club       43.752816       -79.342741   
4            Bruno's valu-mart       43.746143       -79.324630   

         Venue Category  
0  Caribbean Restaurant  
1                  Park  
2                  Café  
3           Golf Course  
4         Grocery Store

In [37]:
len(toronto_venues['Venue'].unique())

1797

In [38]:
map_toronto_venues = folium.Map(location=[latitude, longitude], zoom_start=11.4)

# add markers to map
for lat, lng, venue, neighborhood in zip(toronto_venues['Venue Latitude'], toronto_venues['Venue Longitude'], toronto_venues['Venue'], toronto_venues['Neighborhood']):
    label = '{}, {}'.format(neighborhood, venue)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto_venues)  
    
map_toronto_venues

In [39]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                         
M1B                              29                      29     29   
M1C                               8                       8      8   
M1E                              28                      28     28   
M1G                              20                      20     20   
M1H                              30                      30     30   
...                             ...                     ...    ...   
M9N                              30                      30     30   
M9P                              30                      30     30   
M9R                              30                      30     30   
M9V                              20                      20     20   
M9W                               7                       7      7   

              Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                   
M1B                       29               29              29  
M1C                        8                8               8  
M1E                       28               28              28  
M1G                       20               20              20  
M1H                       30               30              30  
...                      ...              ...             ...  
M9N                       30               30              30  
M9P                       30               30              30  
M9R                       30               30              30  
M9V                       20               20              20  
M9W                        7                7               7  

[99 rows x 6 columns]

In [40]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 276 uniques categories.


In [41]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Zoo Exhibit  Afghan Restaurant  African Restaurant  Airport  \
0            0                  0                   0        0   
1            0                  0                   0        0   
2            0                  0                   0        0   
3            0                  0                   0        0   
4            0                  0                   0        0   

   Airport Lounge  American Restaurant  Amphitheater  Antique Shop  Aquarium  \
0               0                    0             0             0         0   
1               0                    0             0             0         0   
2               0                    0             0             0         0   
3               0                    0             0             0         0   
4               0                    0             0             0         0   

   Arcade  ...  Transportation Service  Turkish Restaurant  \
0       0  ...                       0                   0   
1       0  ...                       0                   0   
2       0  ...                       0                   0   
3       0  ...                       0                   0   
4       0  ...                       0                   0   

   Vegetarian / Vegan Restaurant  Video Game Store  Vietnamese Restaurant  \
0                              0                 0                      0   
1                              0                 0                      0   
2                              0                 0                      0   
3                              0                 0                      0   
4                              0                 0                      0   

   Warehouse Store  Wine Bar  Wings Joint  Women's Store  Yoga Studio  
0                0         0            0              0            0  
1                0         0            0              0            0  
2                0         0            0              0            0  
3                0         0            0              0            0  
4                0         0            0              0            0  

[5 rows x 276 columns]

In [42]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Zoo Exhibit  Afghan Restaurant  African Restaurant  Airport  \
0           M1B     0.068966                0.0            0.034483      0.0   
1           M1C     0.000000                0.0            0.000000      0.0   
2           M1E     0.000000                0.0            0.000000      0.0   
3           M1G     0.000000                0.0            0.000000      0.0   
4           M1H     0.000000                0.0            0.000000      0.0   
..          ...          ...                ...                 ...      ...   
94          M9N     0.000000                0.0            0.000000      0.0   
95          M9P     0.000000                0.0            0.000000      0.0   
96          M9R     0.000000                0.0            0.000000      0.0   
97          M9V     0.000000                0.0            0.000000      0.0   
98          M9W     0.000000                0.0            0.000000      0.0   

    Airport Lounge  American Restaurant  Amphitheater  Antique Shop  Aquarium  \
0              0.0             0.000000           0.0           0.0       0.0   
1              0.0             0.000000           0.0           0.0       0.0   
2              0.0             0.000000           0.0           0.0       0.0   
3              0.0             0.000000           0.0           0.0       0.0   
4              0.0             0.000000           0.0           0.0       0.0   
..             ...                  ...           ...           ...       ...   
94             0.0             0.000000           0.0           0.0       0.0   
95             0.0             0.000000           0.0           0.0       0.0   
96             0.0             0.033333           0.0           0.0       0.0   
97             0.0             0.000000           0.0           0.0       0.0   
98             0.0             0.000000           0.0           0.0       0.0   

    ...  Transportation Service  Turkish Restaurant  \
0   ...                     0.0                 0.0   
1   ...                     0.0                 0.0   
2   ...                     0.0                 0.0   
3   ...                     0.0                 0.0   
4   ...                     0.0                 0.0   
..  ...                     ...                 ...   
94  ...                     0.0                 0.0   
95  ...                     0.0                 0.0   
96  ...                     0.0                 0.0   
97  ...                     0.0                 0.0   
98  ...                     0.0                 0.0   

    Vegetarian / Vegan Restaurant  Video Game Store  Vietnamese Restaurant  \
0                             0.0          0.034483                   0.00   
1                             0.0          0.000000                   0.00   
2                             0.0          0.000000                   0.00   
3                             0.0          0.000000                   0.05   
4                             0.0          0.000000                   0.00   
..                            ...               ...                    ...   
94                            0.0          0.000000                   0.00   
95                            0.0          0.000000                   0.00   
96                            0.0          0.000000                   0.00   
97                            0.0          0.000000                   0.00   
98                            0.0          0.000000                   0.00   

    Warehouse Store  Wine Bar  Wings Joint  Women's Store  Yoga Studio  
0               0.0       0.0     0.000000       0.034483     0.000000  
1               0.0       0.0     0.000000       0.000000     0.000000  
2               0.0       0.0     0.000000       0.000000     0.000000  
3               0.0       0.0     0.000000       0.000000     0.000000  
4               0.0       0.0     0.033333       0.000000     0.033333  
..              ...       ...    

In [43]:
toronto_grouped.shape

(99, 276)

In [44]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----M1B----
                  venue  freq
0           Zoo Exhibit  0.07
1  Fast Food Restaurant  0.07
2            Restaurant  0.07
3                 Trail  0.07
4                  Park  0.03


----M1C----
                venue  freq
0  Italian Restaurant  0.12
1      Breakfast Spot  0.12
2          Playground  0.12
3               Hotel  0.12
4        Burger Joint  0.12


----M1E----
                  venue  freq
0           Pizza Place  0.11
1  Fast Food Restaurant  0.07
2                  Park  0.07
3                  Bank  0.07
4       Automotive Shop  0.04


----M1G----
                  venue  freq
0           Pizza Place  0.15
1           Coffee Shop  0.10
2  Fast Food Restaurant  0.10
3                  Park  0.10
4    Chinese Restaurant  0.05


----M1H----
               venue  freq
0  Indian Restaurant  0.10
1        Coffee Shop  0.07
2         Restaurant  0.07
3               Bank  0.07
4        Gas Station  0.07


----M1J----
                 venue  freq
0       Sandwich Pl

In [45]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [50]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          M1B           Zoo Exhibit  Fast Food Restaurant   
1          M1C                  Park            Playground   
2          M1E           Pizza Place                  Park   
3          M1G           Pizza Place           Coffee Shop   
4          M1H     Indian Restaurant        Sandwich Place   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                 Trail            Restaurant                Bakery   
1  Gym / Fitness Center        Breakfast Spot    Italian Restaurant   
2                  Bank  Fast Food Restaurant  Gym / Fitness Center   
3                  Park  Fast Food Restaurant             Juice Bar   
4            Restaurant           Coffee Shop                  Bank   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                  Bank           Supermarket                   Spa   
1                 Hotel          Burger Joint             Drugstore   
2     Food & Drink Shop           Supermarket            Sports Bar   
3           Music Store        Sandwich Place           Supermarket   
4           Gas Station           Yoga Studio     Fish & Chips Shop   

  9th Most Common Venue 10th Most Common Venue  
0                  Park            Bus Station  
1              Dive Bar                Dog Run  
2            Laundromat             Beer Store  
3      Department Store      Indian Restaurant  
4  Caribbean Restaurant            Music Store

In [51]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 3, 2, 2, 2, 2, 2, 2, 2, 3], dtype=int32)

In [52]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df_scrape

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='PostalCode')

toronto_merged.head() # check the last columns!

PostalCode           Borough                     Neighborhood   Latitude  \
0        M3A        North York                        Parkwoods  43.753259   
1        M4A        North York                 Victoria Village  43.725882   
2        M5A  Downtown Toronto         Regent Park,Harbourfront  43.654260   
3        M6A        North York  Lawrence Manor,Lawrence Heights  43.718518   
4        M9A         Etobicoke                 Islington Avenue  43.667856   

   Longitude  Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
0 -79.329656               3                  Park             Coffee Shop   
1 -79.315572               2           Coffee Shop           Grocery Store   
2 -79.360636               3           Coffee Shop                    Park   
3 -79.464763               0            Restaurant  Furniture / Home Store   
4 -79.532242               3              Pharmacy           Grocery Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0              Pharmacy          Skating Rink              Bus Stop   
1      Asian Restaurant                  Park            Beer Store   
2                Bakery        Breakfast Spot         Historic Site   
3        Clothing Store   Fried Chicken Joint      Department Store   
4                  Park                  Bank            Playground   

  6th Most Common Venue     7th Most Common Venue     8th Most Common Venue  \
0         Shopping Mall                      Bank               Supermarket   
1            Shoe Store            Sandwich Place     Portuguese Restaurant   
2       Thai Restaurant  Mediterranean Restaurant     Performing Arts Venue   
3     Electronics Store               Men's Store  Mediterranean Restaurant   
4        Ice Cream Shop              Skating Rink             Shopping Mall   

  9th Most Common Venue 10th Most Common Venue  
0     Food & Drink Shop        Laundry Service  
1           Pizza Place               Pharmacy  
2          Liquor Store                    Spa  
3         Bowling Alley               Boutique  
4                   Spa               Bus Stop

In [53]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11.4)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters